In [ ]:
## Import necessary packages
%matplotlib osx
# On Macs use osx
# For Windows use qt

#import all libraries
import numpy as np
from numpy.random import rand
from landscape import Landscape # Import methods from inside file landscape.py

from mpl_toolkits.mplot3d import Axes3D
import matplotlib.pyplot as plt
from matplotlib import cm
from matplotlib.animation import FFMpegWriter
from matplotlib.figure import projections

import wave
import array

In [ ]:
### Define simulation grid and initial conditions

# small random features in topography to begin erosion
def initial_conditions(NX,NY):
    Z = rand(NX,NY)
    return Z

NX = 70 #number of rows
NY = 70 #number of columns

d  = 5 # grid spacing in meters
dx = d # keep dx=dy for simplicity
dy = d

LX=NX*dx
LY=NY*dy

Z = initial_conditions(NX,NY) 

x = np.arange(NX)
y = np.arange(NY)
X,Y = np.meshgrid(y,x)

In [ ]:
#initializing the landscape with the set dimensions
ls = Landscape(NX,NY)
ls.pool_check(Z,NX,NY)
ls.A = np.zeros((NX,NY))

In [ ]:
# Set-up figure
def init_figure():
    fig = plt.figure(figsize=(12.,6.))
    plt.show()
    return fig

#functions to generate mountain, build up mountain, erode mountain, and update the current mountain state
def generate_mountainous_region(X, Y, center, peak_height, spread):
    return peak_height * 2 * np.exp(-((X - center[0])**2 + (Y - center[1])**2) / (2 * spread**2))

def build_mountain(Z, build_rate=0.1, target_mountain=None):
    for i in range(Z.shape[0]):
        for j in range(Z.shape[1]):
            # Gradually build up the mountain from the ground
            Z[i, j] += build_rate * (Z[i, j] - np.min(Z)) * 0.5
            
            # Ensure the height doesn't exceed the target mountain
            if target_mountain is not None:
                Z[i, j] = min(Z[i, j], target_mountain[i, j])
    return Z

def simulate_erosion(Z, erosion_rate=0.5, iterations=5):
    for _ in range(iterations):
        for i in range(1, Z.shape[0] - 1):
            for j in range(1, Z.shape[1] - 1):
                neighbors = Z[i-1:i+2, j-1:j+2]
                Z[i, j] -= erosion_rate * (Z[i, j] - np.min(neighbors)) * 0.5
    return Z
    
def update_figure_erode(Z, rate=0):
    plt.clf()
    ax1 = fig.add_subplot(121, projection='3d')

    # set the limits of the 3d graph in all dimensions
    vert_exag = 0.9
    ax1.set_xlim3d(0, max(NX, NY))
    ax1.set_ylim3d(0, max(NX, NY))
    ax1.set_zlim3d(0, max(NX, NY) / vert_exag)

    ax1.set_title('Surface Relief x ' + str(vert_exag))

    # Erode the mountain
    Z = simulate_erosion(Z, erosion_rate = rate)

    surf = ax1.plot_surface(X, Y, Z, cmap=cm.terrain, rstride=1, cstride=1,
                            antialiased=False, linewidth=0)

    plt.draw()
    plt.pause(0.01)
    
def update_figure_build(Z, rate=0):
    plt.clf()
    ax1 = fig.add_subplot(121, projection='3d')

    # set the limits of the 3d graph in all dimensions
    vert_exag = 0.9
    ax1.set_xlim3d(0, max(NX, NY))
    ax1.set_ylim3d(0, max(NX, NY))
    ax1.set_zlim3d(0, max(NX, NY) / vert_exag)

    ax1.set_title('Surface Relief x ' + str(vert_exag))

    # Erode the mountain
    Z = build_mountain(Z, build_rate = rate)

    surf = ax1.plot_surface(X, Y, Z, cmap=cm.terrain, rstride=1, cstride=1,
                            antialiased=False, linewidth=0)

    plt.draw()
    plt.pause(0.01)

In [ ]:
# function to convert the audio file to array of amplitudes
def audio_to_amplitude_array(audio_file, max_samples=None):
    with wave.open(audio_file, 'rb') as wf:
        num_channels = wf.getnchannels()
        sample_width = wf.getsampwidth()
        frame_rate = wf.getframerate()
        num_frames = wf.getnframes()

        # Read audio data
        audio_data = wf.readframes(num_frames if max_samples is None else min(max_samples, num_frames))

    # Convert binary data to a NumPy array
    audio_array = np.frombuffer(audio_data, dtype=np.int16)

    # Normalize the values to be between 0 and 2 based on amplitude
    normalized_amplitude = (np.abs(audio_array) / np.max(np.abs(audio_array))) * 2

    return normalized_amplitude

In [ ]:
# pass in audio file to the amplitude array function
# can pick: ShortBowsAudio.wav | MelodyAudio.wav | PlucksAudio.wav
audio_file_path = 'ShortBowsAudio.wav'
amplitude_array = audio_to_amplitude_array(audio_file_path)

print("Array values:")
print(amplitude_array)

In [ ]:
# Assuming you have initialized NX, NY, X, and Y before calling update_figure
fig = init_figure()

# generate the initial mountain in the middle of the landscape
Z = generate_mountainous_region(X, Y, center=(NX/2, NY/2), peak_height=1, spread=10)

# initialize the animation frame capture 
metadata = dict(title = 'Animation for Musical Mountain', artist = 'Matplotlib',commet = '')
writer = FFMpegWriter(fps=10, metadata=metadata,bitrate=200000)
fig = plt.figure(dpi=200)

split_rate = 5000
erode_rate = 0.5
erode_int = 10

rates = np.array(amplitude_array[::split_rate])
np.insert(rates, 0, 0)
np.insert(rates, len(rates), 0)
with writer.saving(fig, "ShortBowsAudio.mp4", dpi = 200):
    
    # Update the figure in a loop to simulate erosion
    for j in range(1, len(rates)):
        change = rates[j] - rates[j - 1]
        print(change)
        
        # if the amplitude increases, build mountain, else erode it
        if change < 0:
            update_figure_erode(Z, rates[j])
            writer.grab_frame()  
        else:
            update_figure_build(Z, rates[j])
            writer.grab_frame()
            

    plt.show()
    writer.grab_frame()
    
    for i in range(erode_int):
        update_figure_erode(Z, erode_rate)
        writer.grab_frame()